In [ ]:
import numpy as np
import tensorflow as tf
import matplotlib.pyplot as plt
from PIL import Image

%matplotlib inline

sess = tf.Session()

# 1.도형 인식 데이터셋 구성하기

In [ ]:
#1
x_data = []
y_data = []

im = 10

for i in range(40) :
    img = Image.open(('shapedata/네모%d.png') % (i+1))
    gray = img.convert('L').resize((im, im))    
    data = np.array( gray, dtype='uint8' )    
    x_data.append(  data.flatten()   )
    y_data.append(0)
    
for i in range(40) :
    img = Image.open(('shapedata/세모%d.png') % (i+1))
    gray = img.convert('L').resize((im, im))    
    data = np.array( gray, dtype='uint8' )    
    x_data.append(  data.flatten()   )
    y_data.append(1)
    
for i in range(40) :
    img = Image.open(('shapedata/원%d.png') % (i+1))
    gray = img.convert('L').resize((im, im))    
    data = np.array( gray, dtype='uint8' )    
    x_data.append(  data.flatten()   )
    y_data.append(2)
    
x_data = np.array(x_data) / 255.0
y_data = np.array(y_data)
print(x_data.shape)
print(y_data.shape)

In [ ]:
#2
#  0 -> [ 100 ]   1-> [ 0 1 0 ]
def one_hot(y, nclass) :
    r = y.shape[0]
    mat = np.zeros([r, nclass])
    for i in range(r) :
        mat[i, int(y[i])] = 1        
    return mat

y_data_onehot = one_hot(y_data, 3)
print(y_data.shape)
print(y_data[0:5])
print(y_data_onehot.shape)
print(y_data_onehot[0:5, :])

In [ ]:
#3
plt.figure(figsize=(10,10))
for i  in range(60) :
    plt.subplot(12, 5, i+1)
    plt.imshow(x_data[i,:].reshape(im,im), cmap='gray')

In [ ]:
#4

def split(x_data, y_data, rate) :
    n = x_data.shape[0]
    arr = np.arange(n)  
    np.random.shuffle(arr)

    n0 = int(n * rate)
    x_train = x_data[arr[0:n0], :]
    y_train = y_data[arr[0:n0], :]
    x_test =  x_data[arr[n0:], :]
    y_test =  y_data[arr[n0::], :]
    
    return (x_train, y_train, x_test, y_test)

x_train, y_train, x_test, y_test = split(x_data, y_data_onehot, 0.8)

print(x_train.shape, y_train.shape)
print(x_test.shape, y_test.shape)

# 2. 도형인식을 위한 컨볼루션 신경망

In [ ]:
#1
nclass = 3
dim = im * im
nfilter = 32
nhidden = 300

x = tf.placeholder("float", shape=[None, dim])
y = tf.placeholder("float", shape=[None, nclass])

x_image = tf.reshape(x, [-1,im,im,1])

In [ ]:
#2
filter = tf.Variable(tf.random_normal([3, 3, 1, nfilter], stddev=0.1))
b = tf.Variable(tf.constant(0.1, shape=[nfilter]))
conv = tf.nn.sigmoid(tf.nn.conv2d(x_image, filter, strides=[1, 1, 1, 1], padding='SAME') + b)
print(conv.shape)

In [ ]:
#3
pool = tf.nn.max_pool(conv, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')
print(pool.shape)

In [ ]:
#4
h_flat = tf.reshape(pool, [-1, int(im/2) * int(im/2) * nfilter])

w_fc = tf.Variable(tf.random_normal([int(im/2) * int(im/2) * nfilter, nhidden], stddev=0.1))   #1250
b_fc = tf.Variable(tf.constant(0.1, shape=[nhidden]))

h_fc = tf.sigmoid(tf.matmul(h_flat, w_fc) + b_fc)

print(pool.shape)
print(h_flat.shape)
print(w_fc.shape)
print(h_fc.shape)

In [ ]:
#5
w_out = tf.Variable(tf.random_normal([nhidden, nclass], stddev=0.1))
b_out = tf.Variable(tf.constant(0.1, shape=[nclass]))

logits = tf.matmul(h_fc, w_out) + b_out

print(w_out.shape)
print(logits.shape)

In [ ]:
#6
hypothesis = tf.nn.softmax(logits)

cost = -tf.reduce_mean(y*tf.log(hypothesis))
update = tf.train.GradientDescentOptimizer(0.1).minimize(cost)

    

# argmax    :  [ 0.2   0.1   0.7    ]   -> 2
predicted = tf.argmax(hypothesis, 1)

#predict 
#  equal  [  1 1  1 1   ] ==  [ 0 0 1 1 ]   ->  [ false false true rue]
#  cast [ false false true true ]  ->  [ 0 0 1 1 ]
# reduce_mean[ 0 0 1 1] -> 2/4 = 0.5
accuracy = tf.reduce_mean(tf.cast(tf.equal(predicted, tf.argmax(y, 1)), tf.float32))

In [ ]:
#7
print(filter.shape)
print(b.shape)
print(w_fc.shape)
print(b_fc.shape)
print(w_out.shape)
print(b_out.shape)

In [ ]:
#8
sess.run(tf.global_variables_initializer())

for i in range(6001) :    
    sess.run(update,feed_dict={x: x_train, y: y_train})
    
    if i % 300 == 0 :
        a, c = sess.run([accuracy, cost], feed_dict={ x:x_test, y: y_test})
        print(i, "test : ",  a, c)    
a = sess.run(accuracy, feed_dict={ x:x_train, y: y_train})     
print(a)

# 3. 함수로 정리하기

In [ ]:
#1
def convolutionLayer(input, nfilter, sfilter) :
    
    size = input.shape.as_list() 
    nhidden = size[3]       
    
    filter = tf.Variable(tf.random_normal([sfilter, sfilter, nhidden, nfilter], stddev=0.1))
    b = tf.Variable(tf.constant(0.1, shape=[nfilter]))
    conv = tf.nn.sigmoid(tf.nn.conv2d(input, filter, strides=[1, 1, 1, 1], padding='SAME') + b)
    pool = tf.nn.max_pool(conv, ksize=[1, 2, 2, 1], strides=[1, 2, 2, 1], padding='SAME')    
    return pool

In [ ]:
#2
def neuralnetworkLayer(pool, nhidden) :
    
    size = pool.shape.as_list()    
    flatten =  size[1] *  size[2] * size[3]
    
    h_flatten = tf.reshape(pool, [-1, flatten])
    
    w_fc = tf.Variable(tf.random_normal([flatten, nhidden], stddev=0.1))
    b_fc = tf.Variable(tf.constant(0.1, shape=[nhidden]))
    
    h_fc = tf.nn.sigmoid(tf.matmul(h_flatten, w_fc) + b_fc)
    
    
    return  h_fc    

In [ ]:
#3    
def outputLayer(h_fc, nclass) :            
    size = h_fc.shape.as_list()        
    nhidden = size[1]
    w_fc = tf.Variable(tf.random_normal([nhidden, nclass], stddev=0.1))
    b_fc = tf.Variable(tf.constant(0.1, shape=[nclass]))
    logits = tf.matmul(h_fc, w_fc) + b_fc
    return  logits

In [ ]:
#4
pool = convolutionLayer(x_image, 32, 3)
hidden = neuralnetworkLayer(pool, 300)
logits = outputLayer(hidden, 3)

print(x_image.shape)
print(pool.shape)
print(hidden.shape)
print(logits.shape)

In [ ]:
#5
hypothesis = tf.nn.softmax(logits)

cost = -tf.reduce_mean(y*tf.log(hypothesis))
update = tf.train.GradientDescentOptimizer(0.1).minimize(cost)

predicted = tf.argmax(hypothesis, 1)

accuracy = tf.reduce_mean(tf.cast(tf.equal(predicted, tf.argmax(y, 1)), tf.float32))

sess.run(tf.global_variables_initializer())

for i in range(6001) :    
    sess.run(update,feed_dict={x: x_train, y: y_train})
    
    if i % 300 == 0 :
        a, c = sess.run([accuracy, cost], feed_dict={ x:x_test, y: y_test})
        print(i, "test : ",  a, c)    
a = sess.run(accuracy, feed_dict={ x:x_train, y: y_train})     
print(a)

# 4. 다층 구조로 일반화 시키기

In [ ]:
#1
def neuralnetworkLayer2(hidden, nhidden) :  #from 1d  to 1d
    
    size = hidden.shape.as_list()        
    prehidden = size[1]
    
    w_fc = tf.Variable(tf.random_normal([prehidden, nhidden], stddev=0.1))
    b_fc = tf.Variable(tf.constant(0.1, shape=[nhidden]))
    h_fc = tf.nn.sigmoid(tf.matmul(hidden, w_fc) + b_fc)
    return  h_fc    
    
    

In [ ]:
#2
pool = convolutionLayer(x_image, 32,3 )
pool2 = convolutionLayer(pool, 64,3 )
hidden  = neuralnetworkLayer(pool2, 300)
hidden2  = neuralnetworkLayer2(hidden, 100)
logits = outputLayer(hidden2, 3)


print(x_image.shape)
print(pool.shape)
print(pool2.shape)
print(hidden.shape)
print(hidden2.shape)
print(logits.shape)

In [ ]:
#3
hypothesis = tf.nn.softmax(logits)

cost = -tf.reduce_mean(y*tf.log(hypothesis))
update = tf.train.GradientDescentOptimizer(0.1).minimize(cost)

predicted = tf.argmax(hypothesis, 1)

accuracy = tf.reduce_mean(tf.cast(tf.equal(predicted, tf.argmax(y, 1)), tf.float32))

sess.run(tf.global_variables_initializer())

for i in range(3001) :    
    sess.run(update,feed_dict={x: x_train, y: y_train})
    
    if i % 300 == 0 :
        a, c = sess.run([accuracy, cost], feed_dict={ x:x_test, y: y_test})
        print(i, "test : ",  a, c)    
a = sess.run(accuracy, feed_dict={ x:x_train, y: y_train})     
print(a)

# 5. 결과 분석하기

In [ ]:
#1
h, p = sess.run([hypothesis, predicted], feed_dict={ x:x_test, y: y_test})   

labels = ['S', 'T', 'C']
y_data2 = np.argmax(y_test, axis=1)

print(h.shape)
print(p.shape)
print(y_data2.shape)

In [ ]:
    
plt.figure(figsize=(20, 25))

for i in range(24) :        
  plt.subplot(6, 4*2, i*2+1)
  plt.imshow(x_test[i,:].reshape(im,im), cmap='gray')    
  c =  "blue" if  p[i] == y_data2[i]   else "red"    
  plt.subplot(6, 4*2, i*2+2)
  plt.bar(labels, h[i], color=c)
  plt.xlabel("{}-> {} {:2.0f}%".format(labels[int(y_data2[  i ])], labels[p[  i ]],        100*np.max(h[i], axis=0)),  color = c )   
    